## Import

In [69]:
import math
import pandas as pd
import numpy as np
import seaborn as sns

from scipy.sparse import csr_matrix
import matplotlib.pyplot as plt

from surprise import Reader, Dataset, SVD
from surprise import KNNBasic
from surprise import accuracy
from surprise import accuracy

from surprise.model_selection import cross_validate
from surprise.model_selection import train_test_split

from sklearn.metrics import precision_score, recall_score, f1_score
from sklearn.metrics.pairwise import cosine_similarity

from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Embedding, Flatten, Dense, Concatenate,Dot

sns.set_style("darkgrid")

### Importare dataset

In [82]:
df1 = pd.read_csv('./combined_data_1.txt', header = None, names = ['Cust_Id', 'Rating'], usecols = [0,1])

df1['Rating'] = df1['Rating'].astype(float)

print('Dataset 1 shape:',df1.shape)

# Mi genera un nuovo indice da 1
df1 = df1.reset_index()
print('Dataset 1 shape without rating null:',df1.shape)

print('-Dataset examples-')
print(df1[:5])


Dataset 1 shape: (24058263, 2)
Dataset 1 shape without rating null: (24058263, 3)
-Dataset examples-
   index  Cust_Id  Rating
0      0       1:     NaN
1      1  1488844     3.0
2      2   822109     5.0
3      3   885013     4.0
4      4    30878     4.0


### Prendo i primi x , così che il calcolo del film non sia lunghissimo ma genero tante colonne di film

In [83]:
#df1 = df1.head(5000000)
df1 = df1.head(1000000)

### df_nan è un DataFrame che indica True per le righe in cui la colonna 'Rating' è nulla e False altrimenti. Quindi, ogni volta che c'è una transizione da False a True nella colonna 'Rating', rappresenta l'inizio di un nuovo "film"

In [84]:
df_nan = pd.DataFrame(pd.isnull(df1.Rating))
df_nan = df_nan[df_nan['Rating'] == True]
df_nan = df_nan.reset_index()

movie_np = []
movie_id = 1

for i,j in zip(df_nan['index'][1:],df_nan['index'][:-1]):
    # numpy approach
    temp = np.full((1,i-j-1), movie_id)
    movie_np = np.append(movie_np, temp)
    movie_id += 1

# Account for last record and corresponding length
# numpy approach
last_record = np.full((1,len(df1) - df_nan.iloc[-1, 0] - 1),movie_id)
movie_np = np.append(movie_np, last_record)

#print('Movie numpy:',movie_np)
#print('Length:',len(movie_np))

df = df1[pd.notnull(df1['Rating'])]

df['Movie_Id'] = movie_np.astype(int)
df['Cust_Id'] = df['Cust_Id'].astype(int)
print('-Dataset examples-')
print(df)


-Dataset examples-
         index  Cust_Id  Rating  Movie_Id
1            1  1488844     3.0         1
2            2   822109     5.0         1
3            3   885013     4.0         1
4            4    30878     4.0         1
5            5   823519     3.0         1
...        ...      ...     ...       ...
999995  999995  1196927     3.0       225
999996  999996   528854     5.0       225
999997  999997   962705     3.0       225
999998  999998  1299323     2.0       225
999999  999999  2026970     4.0       225

[999775 rows x 4 columns]


/tmp/ipykernel_4752/110950279.py:24: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Movie_Id'] = movie_np.astype(int)
/tmp/ipykernel_4752/110950279.py:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['Cust_Id'] = df['Cust_Id'].astype(int)


### Creo matrice di rating

In [5]:
ratings_matrix = df.pivot(index='Cust_Id', columns='Movie_Id', values='Rating')

# Se vuoi gestire eventuali valori mancanti con uno zero, puoi utilizzare il metodo fillna
ratings_matrix = ratings_matrix.fillna(0)

# Se preferisci avere la matrice come array numpy, puoi utilizzare values
#ratings_matrix_array = ratings_matrix.values

print(ratings_matrix)

Movie_Id  1    2    3    4    5    6    7    8    9    10   ...  216  217  \
Cust_Id                                                     ...             
6         0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
7         0.0  0.0  0.0  0.0  0.0  0.0  0.0  5.0  0.0  0.0  ...  0.0  0.0   
10        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
25        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
33        0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
...       ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...  ...   
2649401   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
2649404   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
2649409   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   
2649426   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  4.0  0.0   
2649429   0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...  0.0  0.0   

### Prendo i primi y così che anche lo user based ha tanti film (un buon profilo ricco) ma riduzo il numero di utenti per non renderlo infinito

In [6]:
ratings_matrix = ratings_matrix.head(10000)

### rimuovo le righe nulle

In [7]:
print(ratings_matrix.shape)

(10000, 225)


In [76]:
ratings_matrix_support = pd.DataFrame()
for i in ratings_matrix.iterrows():
    val = [not(j) for j in i[1]]
    #print(i[1])
    #print(all(val))
    if not(all(val)):
        ratings_matrix_support = ratings_matrix_support.append(i[1])

/tmp/ipykernel_9827/3795530229.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  ratings_matrix_support = ratings_matrix_support.append(i[1])
/tmp/ipykernel_9827/3795530229.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  ratings_matrix_support = ratings_matrix_support.append(i[1])
/tmp/ipykernel_9827/3795530229.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  ratings_matrix_support = ratings_matrix_support.append(i[1])
/tmp/ipykernel_9827/3795530229.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  ratings_matrix_support = ratings_matrix_support.append(i[1])
/tmp/ipykernel_9827/3795530229.py:7: FutureWarning: The frame.append

KeyboardInterrupt: 

In [143]:
#ratings_matrix = ratings_matrix_support.copy()
print(ratings_matrix_support.shape)

(1000, 225)


# Creo Test set

### prendo il rating da colore che ne hanno almeno due e lo metto a 0

In [8]:
y_test = {}
count = 0
for i in ratings_matrix.iterrows():
    if count < 20:
        almenoUno = 0
        for j in range(1,len(i[1])):
            if i[1][j] != 0:
                if almenoUno:
                    y_test[(i[0],j)] = i[1][j]
                    i[1][j] = 0
                    count +=1
                    break
                else:
                    almenoUno= True
            

In [10]:
y_test

{(6, 157): 3.0,
 (7, 28): 4.0,
 (10, 191): 4.0,
 (42, 191): 3.0,
 (59, 180): 2.0,
 (79, 84): 3.0,
 (87, 111): 2.0,
 (97, 167): 4.0,
 (134, 55): 5.0,
 (183, 197): 4.0,
 (188, 108): 3.0,
 (192, 213): 4.0,
 (195, 175): 5.0,
 (199, 111): 4.0,
 (201, 30): 5.0,
 (261, 191): 2.0,
 (265, 30): 5.0,
 (266, 175): 5.0,
 (268, 58): 5.0,
 (283, 148): 1.0}

#### Calcolo rating medi degli utenti

In [11]:
rating_medi = {}
# calcolo rating medio senza considerare gli 0
for i in ratings_matrix.iterrows():
        # somma elementi != 0
        count = 0
        # quanti elementi
        countn = 0
        for j in i[1].values:
            # se non è 0
            if j != 0:
                  count += j
                  countn += 1
        if countn != 0:
                rating_medi[i[0]] = count/countn
        else:
                rating_medi[i[0]] = 0

print(rating_medi)

{6: 3.4, 7: 4.666666666666667, 10: 3.5, 25: 3.0, 33: 4.0, 42: 4.0, 59: 3.5, 79: 2.5, 87: 3.5, 94: 2.0, 97: 3.5, 116: 4.0, 131: 2.0, 134: 4.857142857142857, 158: 3.0, 164: 5.0, 168: 4.0, 169: 4.0, 178: 3.0, 183: 4.0, 188: 3.1666666666666665, 192: 3.0, 195: 4.5, 199: 4.0, 201: 3.5, 242: 4.0, 247: 4.0, 261: 4.0, 265: 3.3333333333333335, 266: 4.0, 268: 5.0, 283: 4.0, 291: 3.0, 296: 3.6666666666666665, 298: 3.5, 301: 4.0, 302: 5.0, 304: 4.0, 305: 3.3333333333333335, 307: 3.3333333333333335, 330: 3.6666666666666665, 333: 5.0, 352: 5.0, 363: 5.0, 383: 3.3333333333333335, 384: 4.0, 416: 5.0, 424: 3.75, 437: 2.8333333333333335, 439: 2.5, 440: 4.0, 442: 3.5, 462: 2.6, 471: 3.0, 477: 3.5, 478: 3.0, 481: 4.25, 491: 3.0, 492: 4.0, 508: 4.0, 527: 3.857142857142857, 536: 4.333333333333333, 546: 3.5, 561: 3.75, 578: 3.0, 585: 3.0, 592: 3.6, 596: 4.0, 602: 4.2, 609: 4.25, 614: 3.3333333333333335, 624: 4.0, 660: 4.0, 663: 4.0, 664: 3.6666666666666665, 682: 4.0, 684: 4.1, 685: 3.0, 688: 5.0, 695: 2.5, 71

## Usare user based NN

### fun di similarità

In [12]:
# Definire la funzione per il calcolo della similarità tra utenti utilizzando la person coefficent
def user_similarity(ratings,user_target,id_user_target):
    similarità = {}
    # scorro UTENTI
    for i in ratings.iterrows():
        # se l'UTENTE è diverso dall'utente target
        if i[0] != id_user_target:
            # calcolo similarità
            numeratore = 0
            denominatoreP1 = 0
            denominatoreP2 = 0

            # scorro recensioni dell'utente
            for j in i[1].keys():

                diffUtenteNoTarg = i[1][j]-rating_medi[i[0]]
                diffUtenteTarg = user_target[j]-rating_medi[id_user_target]

                numeratore += ((diffUtenteNoTarg)*(diffUtenteTarg))
                denominatoreP1 += (diffUtenteNoTarg**2)
                denominatoreP2 += (diffUtenteTarg**2)
            
            sim = 0
            if denominatoreP1 !=0 and denominatoreP2 != 0:
                sim = numeratore/(math.sqrt(denominatoreP1)*math.sqrt(denominatoreP2))
            
            similarità[(i[0],id_user_target)] = sim
    return similarità

### pre-processing sulla similarità

In [13]:
similarita_coppie = {}
for i,_ in y_test:
    # Calcolare la similarità per utenti del tewt set
    similarita_coppie.update(user_similarity(ratings_matrix,ratings_matrix.loc[i],i))

In [14]:
similarita_coppie

{(7, 6): 0.9875805968075406,
 (10, 6): 0.993358800656939,
 (25, 6): 0.9855195059770339,
 (33, 6): 0.9894901728020767,
 (42, 6): 0.9911756710275614,
 (59, 6): 0.9884668290322656,
 (79, 6): 0.9858727020225875,
 (87, 6): 0.9895146596158011,
 (94, 6): 0.9855195059770283,
 (97, 6): 0.9888111485861761,
 (116, 6): 0.9894901728020767,
 (131, 6): 0.9921372840187758,
 (134, 6): 0.9743010929906664,
 (158, 6): 0.9855195059770339,
 (164, 6): 0.9921372840187797,
 (168, 6): 0.9894901728020767,
 (169, 6): 0.9881666171937272,
 (178, 6): 0.9894901728020822,
 (183, 6): 0.9894901728020767,
 (188, 6): 0.9796592643963675,
 (192, 6): 0.9855195059770339,
 (195, 6): 0.9861097823278384,
 (199, 6): 0.9933549330596739,
 (201, 6): 0.9807726925069574,
 (242, 6): 0.9855195059770283,
 (247, 6): 0.9881666171937272,
 (261, 6): 0.9894901728020767,
 (265, 6): 0.9807756725665019,
 (266, 6): 0.9898491511252226,
 (268, 6): 0.9855195059770322,
 (283, 6): 0.9894901728020767,
 (291, 6): 0.9881666171937329,
 (296, 6): 0.9851492

In [84]:
utenteSimileUno = ratings_matrix.loc[261]
utenteSimileDue = ratings_matrix.loc[2044720]
print(utenteSimileUno)
print(utenteSimileDue)
print(user_target)


Movie_Id
1     0.0
2     0.0
3     0.0
4     0.0
5     0.0
6     0.0
7     0.0
8     0.0
9     0.0
10    0.0
11    0.0
12    0.0
13    0.0
14    0.0
15    0.0
16    0.0
17    0.0
18    0.0
19    0.0
20    0.0
21    0.0
22    0.0
23    0.0
24    0.0
25    0.0
26    0.0
27    0.0
28    0.0
29    0.0
30    4.0
Name: 261, dtype: float64
Movie_Id
1     0.0
2     0.0
3     0.0
4     0.0
5     0.0
6     0.0
7     0.0
8     1.0
9     0.0
10    0.0
11    0.0
12    0.0
13    0.0
14    0.0
15    0.0
16    0.0
17    1.0
18    0.0
19    0.0
20    0.0
21    0.0
22    0.0
23    0.0
24    0.0
25    0.0
26    0.0
27    0.0
28    0.0
29    0.0
30    4.0
Name: 2044720, dtype: float64
Movie_Id
1     0.0
2     0.0
3     0.0
4     0.0
5     0.0
6     0.0
7     0.0
8     0.0
9     0.0
10    0.0
11    0.0
12    0.0
13    0.0
14    0.0
15    0.0
16    0.0
17    0.0
18    0.0
19    0.0
20    0.0
21    0.0
22    0.0
23    0.0
24    0.0
25    0.0
26    0.0
27    0.0
28    0.0
29    0.0
30    3.0
Name: 2442, dtype

In [15]:
# FACCIO UNA SOGLIO K DI VICINATO SULLA BASE DELLA SIMILARITÀ
def calcoloSimilaritaConSoglia(similarita,id_user_target):
    sim_soglia = {}
    # scorro coppie di similarità (a,b)
    for i in similarita:
        # se la similarità rispetta la soglia
        if similarita[i] > 0.95:
            # verifico che sia del mio utente target
            if i[1] == id_user_target:
                sim_soglia[i] = similarita[i]
    return sim_soglia

#### fun Prediction

In [16]:
# Definire una funzione per la predizione delle valutazioni utilizzando User-Based Collaborative Filtering
def predict_user_based(item,user_similarities,ratings_matrix,rating_medi,id_user_target):
    # Calcolare le valutazioni previste
    num = 0
    den = 0
    pred_ratings = 0
    
    for i in user_similarities:     
        
        num += (user_similarities[i]* (ratings_matrix.loc[i[0]][item]-rating_medi[i[0]]))
        den += user_similarities[i]

    if den != 0:
        pred_ratings = rating_medi[id_user_target] + (num / den)
    else:
        pred_ratings = rating_medi[id_user_target]
        
    #print(pred_ratings)
    return pred_ratings
    #else:
    #    return ratings_matrix.loc[id_user_target][item]

# Ottenere le previsioni per tutte le valutazioni
#predicted_ratings_user_based = predict_user_based(id_item_target, sim_soglia,ratings_matrix,rating_medi,id_user_target)
#print(f'Rating per l item {id_item_target} è di {predicted_ratings_user_based} per l utente {id_user_target}')


### testing model

In [17]:
# Ottenere le previsioni per tutte le valutazioni
y_pred = {}

for i in y_test:
    print(f'{i} starting...')

    # vettore rating utente target
    print(f'user target processing...')
    user_target = ratings_matrix.loc[i[0]]
    # SIMILARITÀ SOPRA CERTA SOGLIA
    print('sim_soglia processing...')
    sim_soglia = calcoloSimilaritaConSoglia(similarita_coppie,i[0])
    print(len(sim_soglia))
    # predico rating test
    print('predicting...')
    predicted_ratings_user_based = predict_user_based(i[1], sim_soglia, ratings_matrix,rating_medi,i[0])   
    if predicted_ratings_user_based < 0:
        predicted_ratings_user_based = 0
    # rating predetto
    print('Appending...')
    y_pred[i]=round(predicted_ratings_user_based,2)


(6, 157) starting...
user target processing...
sim_soglia processing...
9949
predicting...
Appending...
(7, 28) starting...
user target processing...
sim_soglia processing...
9950
predicting...
Appending...
(10, 191) starting...
user target processing...
sim_soglia processing...
9952
predicting...
Appending...
(42, 191) starting...
user target processing...
sim_soglia processing...
9953
predicting...
Appending...
(59, 180) starting...
user target processing...
sim_soglia processing...
9960
predicting...
Appending...
(79, 84) starting...
user target processing...
sim_soglia processing...
9946
predicting...
Appending...
(87, 111) starting...
user target processing...
sim_soglia processing...
9948
predicting...
Appending...
(97, 167) starting...
user target processing...
sim_soglia processing...
9951
predicting...
Appending...
(134, 55) starting...
user target processing...
sim_soglia processing...
9946
predicting...
Appending...
(183, 197) starting...
user target processing...
sim_soglia

In [18]:
print(f'y_pred:{y_pred}')
print(f'y_test:{y_test}')

y_pred:{(6, 157): 0, (7, 28): 1.45, (10, 191): 1.16, (42, 191): 1.66, (59, 180): 0, (79, 84): 0, (87, 111): 0.11, (97, 167): 0, (134, 55): 1.16, (183, 197): 1.28, (188, 108): 0, (192, 213): 0, (195, 175): 2.07, (199, 111): 0.61, (201, 30): 1.34, (261, 191): 1.65, (265, 30): 1.17, (266, 175): 1.57, (268, 58): 1.49, (283, 148): 0.53}
y_test:{(6, 157): 3.0, (7, 28): 4.0, (10, 191): 4.0, (42, 191): 3.0, (59, 180): 2.0, (79, 84): 3.0, (87, 111): 2.0, (97, 167): 4.0, (134, 55): 5.0, (183, 197): 4.0, (188, 108): 3.0, (192, 213): 4.0, (195, 175): 5.0, (199, 111): 4.0, (201, 30): 5.0, (261, 191): 2.0, (265, 30): 5.0, (266, 175): 5.0, (268, 58): 5.0, (283, 148): 1.0}


### MAE, NMAE, RMSE, Precision, Recall, F1

In [19]:
# i'm deleting the rate predicted for evaluationg sim_soglia
""" for i in range(len(y_true)):rating_medi[id_user_target]
    if y_true[i] == 0:
        y_pred[i] = 0 """

# Calcola le metriche aggiuntive

precision = precision_score([round(y_test[pred]) for pred in y_test], [round(y_pred[pred]) for pred in y_pred], average='micro')
recall = recall_score([round(y_test[pred]) for pred in y_test], [round(y_pred[pred]) for pred in y_pred], average='micro')
f1 = f1_score([round(y_test[pred]) for pred in y_test], [round(y_pred[pred]) for pred in y_pred], average='micro')
#nmae = accuracy.mae(predictions) / (max(y_true) - min(y_true))
#mae = accuracy.mae(y_pred)

def mae(true,pred):
    n = len(true)
    tot_val = 0
    for i in true:
        val = abs(pred[i]-true[i])
        tot_val += val
    print(f'MAE:{(tot_val/n)}')

def Nmae(true,pred):
    n = len(true)
    tot_val = 0
    max = 0
    min = 9999
    for i in true:
        if true[i] < min:
            min = true[i]
        if true[i] > max:
            max = true[i]
        val = abs(pred[i]-true[i])
        tot_val += val
    print(f'NMAE:{(tot_val/(n*(max-min)))}')

def rmse(true,pred):
    n = len(true)
    tot_val = 0
    for i in true:
        val = (pred[i]-true[i])**2
        tot_val += val
    rapp = tot_val/n
    print(f'RMSE:{math.sqrt(rapp)}')

mae(y_test,y_pred)
Nmae(y_test,y_pred)
rmse(y_test,y_pred)

# Stampa i risultati
print(f'Precision:',precision)
print(f'Recall:',recall)
print(f'F1 Score:',f1)
#print(f'NMAE:',nmae)
#print(f'MAE:',mae)

MAE:2.7874999999999996
NMAE:0.6968749999999999
RMSE:2.9803498116831855
Precision: 0.1
Recall: 0.1
F1 Score: 0.10000000000000002


## Usare item based NN 

In [20]:
ratings_matrix_transpose = ratings_matrix.transpose()
#df.pivot(index='Movie_Id', columns='Cust_Id', values='Rating')

# Se vuoi gestire eventuali valori mancanti con uno zero, puoi utilizzare il metodo fillna
ratings_matrix_transpose = ratings_matrix_transpose.fillna(0)

# Se preferisci avere la matrice come array numpy, puoi utilizzare values
#ratings_matrix_array = ratings_matrix.values

print(ratings_matrix_transpose)

Cust_Id   6      7      10     25     33     42     59     79     87     \
Movie_Id                                                                  
1           0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
2           0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
3           0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
4           0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
5           0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
...         ...    ...    ...    ...    ...    ...    ...    ...    ...   
221         0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
222         0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
223         0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
224         0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
225         0.0    0.0    0.0    0.0    0.0    0.0    0.0    2.0    0.0   

Cust_Id   94     ...  93

### fun adjusted cosine similarity

In [21]:
# Definire la funzione per il calcolo della similarità tra utenti utilizzando la person coefficent
def item_similarity(ratings,item_target,id_item_target):
    similarita_transpose = {}
    # scorro UTENTI
    for i in ratings.iterrows():
        # i riga film con rating utenti
        # se l'ITEM è diverso dall'item target
        if i[0] != id_item_target:
            # calcolo similarità
            numeratore = 0
            denominatoreP1 = 0
            denominatoreP2 = 0
            for j in i[1].keys():
                diffFilmNoTarg = i[1][j]-rating_medi[j]
                diffFilmTarg = item_target[j]-rating_medi[j]

                numeratore += ((diffFilmNoTarg)*(diffFilmTarg))
                denominatoreP1 += (diffFilmNoTarg**2)
                denominatoreP2 += (diffFilmTarg**2)
            sim = 0
            if denominatoreP1 != 0 and denominatoreP2 != 0:
                sim = numeratore/(math.sqrt(denominatoreP1)*math.sqrt(denominatoreP2))
            similarita_transpose[(i[0],id_item_target)] = sim

    return similarita_transpose
# Calcolare la similarità tra utenti
#item_similarity(ratings_matrix_transpose,item_target)
#print(similarita_transpose)

### Pre processing similarity

In [22]:
similarita_coppie_transpose = {}
for i,j in y_test:
    #print(i)
    # Calcolare la similarità tra utenti
    similarita_coppie_transpose.update(item_similarity(ratings_matrix_transpose,ratings_matrix_transpose.loc[j],j))

In [23]:
similarita_coppie_transpose

{(1, 157): 0.9976562218349205,
 (2, 157): 0.9987256808427822,
 (3, 157): 0.9950650177221603,
 (4, 157): 0.9987637364271761,
 (5, 157): 0.9964464630936106,
 (6, 157): 0.9978470676855263,
 (7, 157): 0.9989720243591168,
 (8, 157): 0.9775773367719883,
 (9, 157): 0.9989546572775541,
 (10, 157): 0.9987047068044203,
 (11, 157): 0.9987671797197006,
 (12, 157): 0.9983717847330804,
 (13, 157): 0.9985522646271777,
 (14, 157): 0.9987532770609118,
 (15, 157): 0.998420467685395,
 (16, 157): 0.996006589531489,
 (17, 157): 0.9900141420244415,
 (18, 157): 0.9788296835647652,
 (19, 157): 0.9980246434015899,
 (20, 157): 0.9987570298297289,
 (21, 157): 0.9986389376177321,
 (22, 157): 0.9989127957235977,
 (23, 157): 0.9982048799540402,
 (24, 157): 0.9974087564091452,
 (25, 157): 0.9969023400594204,
 (26, 157): 0.9925779378226651,
 (27, 157): 0.9989303138428107,
 (28, 157): 0.9258367523591499,
 (29, 157): 0.9976076318587068,
 (30, 157): 0.7534844900588512,
 (31, 157): 0.9985381931454357,
 (32, 157): 0.99517

In [118]:
# FACCIO UNA SOGLIO K DI VICINATO SULLA BASE DELLA SIMILARITÀ
sim_soglia_transpose = {}
for i in similarita_transpose:
    if similarita_transpose[i] > 0.0:
        sim_soglia_transpose[i] = similarita_transpose[i]
print(sim_soglia_transpose)

{(2, 1): 0.045871176736922314}


### selecting item simili

In [24]:
# prendo solo gli item votati dall'utente target
def similaritaSoglia(similarita_transpose,id_item_target):
    sim_soglia_transpose = {}
    # scorro coppie similirarità
    for i in similarita_transpose:
        # controllo la soglia
        if similarita_transpose[i] > 0.6:
            # controllo se è la similarità del mio target
            if i[1] == id_item_target:
                sim_soglia_transpose[i] = similarita_transpose[i]
    return sim_soglia_transpose

### fun predict

In [25]:
# Definire una funzione per la predizione delle valutazioni utilizzando User-Based Collaborative Filtering
def predict_item_based(user,sim_soglia_transpose,ratings_matrix_transpose,id_item_target):
    # Calcolare le valutazioni previste
    num = 0
    den = 0
    #scorro item simili a tutti i target
    for i in sim_soglia_transpose:
        # controllo che sia simili al target passato
        if i[1] == id_item_target:
            # se l'utente l'ha votato
            if ratings_matrix_transpose.loc[i[0]][user] != 0:
                
                num += (sim_soglia_transpose[i]* (ratings_matrix_transpose.loc[i[0]][user]))
                den += sim_soglia_transpose[i]

    pred_ratings = 0
    if den != 0:
        pred_ratings = (num / den)
    return pred_ratings
    

# Ottenere le previsioni per tutte le valutazioni
#predicted_ratings_user_based = predict_item_based(id_item_target, similarita_transpose,ratings_matrix_transpose,id_item_target)
#print(f'Rating per l item {id_item_target} è di {predicted_ratings_user_based} per l utente {id_user_target}')


### Testing model

In [26]:
# Ottenere le previsioni per tutte le valutazioni
y_pred_transpose = {}

# scorro utenti target
for i in y_test:
    print(f'{i} starting...')
    # vettore rating utente target
    print(f'user target processing...')
    #item_target = ratings_matrix_transpose.loc[i[1]]
    
    print('sim_soglia processing...')
    # SIMILARITÀ SOPRA CERTA SOGLIA
    sim_soglia_transpose = similaritaSoglia(similarita_coppie_transpose,i[1])
    # predico rating test
    print('predicting...')
    predicted_ratings_item_based = predict_item_based(i[0], sim_soglia_transpose, ratings_matrix_transpose,i[1])   
    
    if predicted_ratings_item_based < 0:
        predicted_ratings_item_based = 0
    # rating predetto
    print('Appending...')
    y_pred_transpose[i]=round(predicted_ratings_item_based,2)


(6, 157) starting...
user target processing...
sim_soglia processing...
predicting...
Appending...
(7, 28) starting...
user target processing...
sim_soglia processing...
predicting...
Appending...
(10, 191) starting...
user target processing...
sim_soglia processing...
predicting...
Appending...
(42, 191) starting...
user target processing...
sim_soglia processing...
predicting...
Appending...
(59, 180) starting...
user target processing...
sim_soglia processing...
predicting...
Appending...
(79, 84) starting...
user target processing...
sim_soglia processing...
predicting...
Appending...
(87, 111) starting...
user target processing...
sim_soglia processing...
predicting...
Appending...
(97, 167) starting...
user target processing...
sim_soglia processing...
predicting...
Appending...
(134, 55) starting...
user target processing...
sim_soglia processing...
predicting...
Appending...
(183, 197) starting...
user target processing...
sim_soglia processing...
predicting...
Appending...
(18

In [27]:
print(f'y_pred:{y_pred_transpose}')
print(f'y_true:{y_test}')

y_pred:{(6, 157): 3.43, (7, 28): 4.66, (10, 191): 3.52, (42, 191): 4.0, (59, 180): 3.52, (79, 84): 2.39, (87, 111): 3.38, (97, 167): 3.55, (134, 55): 4.85, (183, 197): 4.0, (188, 108): 3.18, (192, 213): 3.0, (195, 175): 4.46, (199, 111): 3.98, (201, 30): 3.42, (261, 191): 4.0, (265, 30): 3.33, (266, 175): 4.0, (268, 58): 5.0, (283, 148): 4.0}
y_true:{(6, 157): 3.0, (7, 28): 4.0, (10, 191): 4.0, (42, 191): 3.0, (59, 180): 2.0, (79, 84): 3.0, (87, 111): 2.0, (97, 167): 4.0, (134, 55): 5.0, (183, 197): 4.0, (188, 108): 3.0, (192, 213): 4.0, (195, 175): 5.0, (199, 111): 4.0, (201, 30): 5.0, (261, 191): 2.0, (265, 30): 5.0, (266, 175): 5.0, (268, 58): 5.0, (283, 148): 1.0}


### MAE, NMAE, RMSE, Precision, Recall, F1

In [28]:
# i'm deleting the rate predicted for evaluationg sim_soglia
""" for i in range(len(y_true)):
    if y_true[i] == 0:
        y_pred[i] = 0 """


precision = precision_score([round(y_test[pred]) for pred in y_test], [round(y_pred_transpose[pred]) for pred in y_pred_transpose], average='micro')
recall = recall_score([round(y_test[pred]) for pred in y_test], [round(y_pred_transpose[pred]) for pred in y_pred_transpose], average='micro')
f1 = f1_score([round(y_test[pred]) for pred in y_test], [round(y_pred_transpose[pred]) for pred in y_pred_transpose], average='micro')
#nmae = accuracy.mae(predictions) / (max(y_true) - min(y_true))
#mae = accuracy.mae(y_pred)

def mae(true,pred):
    n = len(true)
    tot_val = 0
    for i in pred:
        val = abs(pred[i]-true[i])
        tot_val += val
    print(f'MAE:{(tot_val/n)}')

def Nmae(true,pred):
    n = len(true)
    tot_val = 0
    max = 0
    min = 9999
    for i in pred:
        if true[i] < min:
            min = true[i]
        if true[i] > max:
            max = true[i]
        val = abs(pred[i]-true[i])
        tot_val += val
    print(f'NMAE:{(tot_val/(n*(max-min)))}')

def rmse(true,pred):
    n = len(true)
    tot_val = 0
    for i in pred:
        val = (pred[i]-true[i])**2
        tot_val += val
    rapp = tot_val/n
    print(f'RMSE:{math.sqrt(rapp)}')

mae(y_test,y_pred_transpose)
Nmae(y_test,y_pred_transpose)
rmse(y_test,y_pred_transpose)

# Stampa i risultati
print(f'Precision:',precision)
print(f'Recall:',recall)
print(f'F1 Score:',f1)
#print(f'NMAE:',nmae)
#print(f'MAE:',mae)

MAE:0.8835
NMAE:0.220875
RMSE:1.1677435506137468
Precision: 0.4
Recall: 0.4
F1 Score: 0.4000000000000001


## Paradigma : User based vs item base

## Matrix factorization: SVD 

In [29]:
reader = Reader()

# get just top 100K rows for faster run time
data = Dataset.load_from_df(df[['Cust_Id', 'Movie_Id', 'Rating']][:], reader)
#data.split(n_folds=3)
trainsetData, testsetData = train_test_split(data, test_size=0.2)

In [30]:
svd = SVD()
cross_validate(svd, data, measures=['RMSE', 'MAE'],verbose=True,return_train_measures=True,n_jobs=100)


Evaluating RMSE, MAE of algorithm SVD on 5 split(s).

                  Fold 1  Fold 2  Fold 3  Fold 4  Fold 5  Mean    Std     
RMSE (testset)    0.9864  0.9861  0.9884  0.9863  0.9854  0.9865  0.0010  
MAE (testset)     0.7731  0.7719  0.7746  0.7739  0.7723  0.7731  0.0010  
RMSE (trainset)   0.7441  0.7452  0.7424  0.7443  0.7410  0.7434  0.0015  
MAE (trainset)    0.5799  0.5806  0.5786  0.5804  0.5783  0.5795  0.0009  
Fit time          12.02   10.71   10.86   10.95   16.89   12.29   2.35    
Test time         2.67    1.88    1.78    1.87    1.77    1.99    0.34    


{'test_rmse': array([0.98638103, 0.98611942, 0.98844571, 0.98633678, 0.98537552]),
 'train_rmse': array([0.74408838, 0.74518998, 0.74237323, 0.74426768, 0.74102758]),
 'test_mae': array([0.77309136, 0.77186135, 0.77455396, 0.7738537 , 0.77226737]),
 'train_mae': array([0.57993803, 0.58057068, 0.57855714, 0.580387  , 0.57827521]),
 'fit_time': (12.024286270141602,
  10.705594539642334,
  10.861852884292603,
  10.953738689422607,
  16.88507318496704),
 'test_time': (2.668484926223755,
  1.8777868747711182,
  1.7790920734405518,
  1.8670237064361572,
  1.7693138122558594)}

## NN

In [104]:
xTrain = pd.DataFrame({'Movie_Id': df['Movie_Id'], 'Cust_Id': df['Cust_Id']})
yTrain = pd.DataFrame({'Rating': df['Rating']})

print(xTrain.head())
print(yTrain.head())

   Movie_Id  Cust_Id
1         1  1488844
2         1   822109
3         1   885013
4         1    30878
5         1   823519
   Rating
1     3.0
2     5.0
3     4.0
4     4.0
5     3.0


In [130]:
trainset = trainsetData
testset = testsetData
xyTrain = pd.DataFrame(trainset.all_ratings(), columns=['Cust_Id', 'Movie_Id', 'Rating'])
xTrain = pd.DataFrame({'Movie_Id': xyTrain['Movie_Id'], 'Cust_Id': xyTrain['Cust_Id']})
yTrain = pd.DataFrame({'Rating': xyTrain['Rating']})

In [144]:
xyTest = pd.DataFrame(testset,columns=['Cust_Id', 'Movie_Id', 'Rating'])
xTest = pd.DataFrame({'Movie_Id': xyTest['Movie_Id'], 'Cust_Id': xyTest['Cust_Id']})
yTest = pd.DataFrame({'Rating': xyTest['Rating']})
# Convert DataFrame to numpy arrays
xTest_numpy = {'Cust_Id': np.array(xTest['Cust_Id']), 'Movie_Id': np.array(xTest['Movie_Id'])}
yTest_numpy = np.array(yTest['Rating'])

In [133]:

user_input = Input(shape=(1,), name='Cust_Id')
item_input = Input(shape=(1,), name='Movie_Id')

# Define embedding layers for users and items
user_embedding = Embedding(input_dim=3000000, output_dim=16, input_length=1)(user_input)
item_embedding = Embedding(input_dim=226, output_dim=16, input_length=1)(item_input)

# Flatten the embeddings
user_embedding = Flatten()(user_embedding)
item_embedding = Flatten()(item_embedding)

# Dot product to get the user-item interaction
dot_product = Dot(axes=1, name='dot_product')([user_embedding, item_embedding])

# Dense layers
dense0 = Dense(16, activation='relu')(dot_product)
dense2 = Dense(32, activation='relu')(dense0)

# Output layer with linear activation for regression
output = Dense(1, activation='linear')(dense2)

# Model
model = Model(inputs=[user_input, item_input], outputs=output)

# Compile the model
model.compile(optimizer='adam', loss='mean_squared_error')

# Convert DataFrame to numpy arrays
xTrain_numpy = {'Cust_Id': np.array(xTrain['Cust_Id']), 'Movie_Id': np.array(xTrain['Movie_Id'])}
yTrain_numpy = np.array(yTrain['Rating'])

# Fit the model
history = model.fit(x=xTrain_numpy, y=yTrain_numpy, epochs=1, batch_size=512,validation_split=0.2)


1250/1250 [==============================] - 1099s 878ms/step - loss: 1.8824 - val_loss: 1.1767


In [145]:
# Print MSE for training and validation
train_mse = history.history['loss'][-1]
val_mse = history.history['val_loss'][-1]

print(f'Training MSE: {train_mse}')
print(f'Validation MSE: {val_mse}')

Training MSE: 1.8823546171188354
Validation MSE: 1.1767351627349854


In [146]:
# Evaluate the model
mse = model.evaluate(xTest_numpy,yTest_numpy)
print(f"Mean Squared Error: {mse}")

6249/6249 [==============================] - 7s 1ms/step - loss: 1.2312
Mean Squared Error: 1.2312018871307373


In [149]:
y_pred = model.predict(xTest_numpy)

6249/6249 [==============================] - 6s 973us/step


In [153]:
y_pred
y_pred_custom = []
for i in y_pred:
    y_pred_custom.append(i[0])

In [158]:
#precision = precision_score(yTrain.values, y_pred_custom, average='micro')
#recall = recall_score(yTrain.values, y_pred_custom, average='micro')
#f1 = f1_score(yTrain.values, y_pred_custom, average='micro')


def mae(true,pred):
    n = len(true)
    tot_val = 0
    for i in range(n):
        val = abs(pred[i]-true[i])
        tot_val += val
    print(f'MAE:{(tot_val/n)}')

def Nmae(true,pred):
    n = len(true)
    tot_val = 0
    max = 0
    min = 9999
    for i in range(n):
        if true[i] < min:
            min = true[i]
        if true[i] > max:
            max = true[i]
        val = abs(pred[i]-true[i])
        tot_val += val
    print(f'NMAE:{(tot_val/(n*(max-min)))}')

def rmse(true,pred):
    n = len(true)
    tot_val = 0
    for i in range(n):
        val = (pred[i]-true[i])**2
        tot_val += val
    rapp = tot_val/n
    print(f'RMSE:{math.sqrt(rapp)}')

mae(yTest_numpy,y_pred_custom)
Nmae(yTest_numpy,y_pred_custom)
rmse(yTest_numpy,y_pred_custom)

# Stampa i risultati
print(f'Precision:',precision)
print(f'Recall:',recall)
print(f'F1 Score:',f1)
#print(f'NMAE:',nmae)
#print(f'MAE:',mae)

3.0
3.327941
4.0
3.366163
4.0
3.308397
1.0
3.3255181
1.0
3.33221
2.0
3.327962
4.0
3.448663
3.0
3.4301403
3.0
3.337391
4.0
3.3111234
4.0
3.3534012
1.0
3.3052983
3.0
3.3194547
3.0
3.3113859
5.0
3.4038506
3.0
3.3471093
5.0
3.3242416
4.0
3.317999
1.0
3.5242383
2.0
3.458898
5.0
3.3576386
4.0
3.3177097
4.0
3.447828
3.0
3.3372447
3.0
3.3400838
4.0
3.3982644
4.0
3.3126783
5.0
3.360005
2.0
3.3064659
4.0
3.3538556
4.0
3.3932657
3.0
3.3771935
5.0
3.7871556
5.0
3.3288434
5.0
3.3311698
5.0
3.302905
3.0
3.330863
5.0
3.36725
4.0
3.3042626
3.0
3.4205241
4.0
3.3098583
4.0
3.3674572
4.0
3.3514867
2.0
3.3246098
3.0
3.330904
5.0
3.362131
3.0
3.5927742
3.0
3.3327787
5.0
3.3800128
3.0
3.3724544
1.0
3.3124537
1.0
3.4332886
3.0
3.62434
4.0
3.3853052
4.0
3.5644898
5.0
3.3176668
4.0
3.4002476
5.0
3.3535466
5.0
3.3622818
4.0
3.3065155
2.0
3.3273969
4.0
3.4048467
1.0
3.3297558
5.0
3.325477
4.0
3.3452256
4.0
3.3494222
3.0
3.3415546
1.0
3.3089027
4.0
3.4985642
4.0
3.3028164
2.0
3.3685138
4.0
3.3227806
4.0
3.327083
